# 機械学習入門授業課題 信用情報の学習

### 参考URL
### https://medium.com/thecyphy/home-credit-default-risk-part-1-3bfe3c7ddd7a

In [87]:
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import numpy as np
from scipy.stats import kurtosis
from scipy.stats import skew
import pylab as pl
%matplotlib inline
!pip install lightgbm




In [441]:
application_train = pd.read_csv('application_train.csv')
application_test = pd.read_csv('application_test.csv')

In [3]:
app_train = pd.DataFrame(app_train)
app_test = pd.DataFrame(app_test)

print(app_train.shape)
print(app_test.shape)

(307511, 122)
(48744, 121)


## 【問題1】コンペティション内容の確認
コンペティションのOverviewページ読み、「Home Credit Default Risk」について以下の観点について確認してください。


- 何を学習し、何を予測するのか

→application_trainのデータを学習し、融資して返済される確率を予測する。


- どのようなファイルを作りKaggleに提出するか

→IDと予測確率を2列にしたもの。


- 提出されたものはどういった指標値で評価されるのか

→ROC曲線　（真陽性率（=TPF）と偽陽性率（=FPF）を計算し、縦軸にTPF、横軸にFPFをとった平面にプロットして線で結んで表す。ROC曲線を作成した時に、グラフの下の部分の面積をAUC（Area Under the Curve）とよぶ。他線が存在しても依存しない。AUCは0から1までの値をとり、値が1に近いほど判別能が高いことを示す。）

http://www.med.osaka-u.ac.jp/pub/kid/clinicaljournalclub6.html

## 【問題2】学習と検証
データを簡単に分析、前処理し、学習、検証するまでの一連の流れを作成・実行してください。


検証にはこのコンペティションで使用される評価指標を用いるようにしてください。学習に用いる手法は指定しません。




In [4]:
app_train.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 307511 entries, 0 to 307510
Columns: 122 entries, SK_ID_CURR to AMT_REQ_CREDIT_BUREAU_YEAR
dtypes: float64(65), int64(41), object(16)
memory usage: 286.2+ MB


In [5]:
app_test.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 48744 entries, 0 to 48743
Columns: 121 entries, SK_ID_CURR to AMT_REQ_CREDIT_BUREAU_YEAR
dtypes: float64(65), int64(40), object(16)
memory usage: 45.0+ MB


In [6]:
app_train.describe()

SK_ID_CURR         TARGET   CNT_CHILDREN  AMT_INCOME_TOTAL  \
count  307511.000000  307511.000000  307511.000000      3.075110e+05   
mean   278180.518577       0.080729       0.417052      1.687979e+05   
std    102790.175348       0.272419       0.722121      2.371231e+05   
min    100002.000000       0.000000       0.000000      2.565000e+04   
25%    189145.500000       0.000000       0.000000      1.125000e+05   
50%    278202.000000       0.000000       0.000000      1.471500e+05   
75%    367142.500000       0.000000       1.000000      2.025000e+05   
max    456255.000000       1.000000      19.000000      1.170000e+08   

         AMT_CREDIT    AMT_ANNUITY  AMT_GOODS_PRICE  \
count  3.075110e+05  307499.000000     3.072330e+05   
mean   5.990260e+05   27108.573909     5.383962e+05   
std    4.024908e+05   14493.737315     3.694465e+05   
min    4.500000e+04    1615.500000     4.050000e+04   
25%    2.700000e+05   16524.000000     2.385000e+05   
50%    5.135310e+05   24903.000000     4.500000e+05   
75%    8.086500e+05   34596.000000     6.795000e+05   
max    4.050000e+06  258025.500000     4.050000e+06   

       REGION_POPULATION_RELATIVE     DAYS_BIRTH  DAYS_EMPLOYED  \
count               307511.000000  307511.000000  307511.000000   
mean                     0.020868  -16036.995067   63815.045904   
std                      0.013831    4363.988632  141275.766519   
min                      0.000290  -25229.000000  -17912.000000   
25%                      0.010006  -19682.000000   -2760.000000   
50%                      0.018850  -15750.000000   -1213.000000   
75%                      0.028663  -12413.000000    -289.000000   
max                      0.072508   -7489.000000  365243.000000   

       DAYS_REGISTRATION  DAYS_ID_PUBLISH    OWN_CAR_AGE     FLAG_MOBIL  \
count      307511.000000    307511.000000  104582.000000  307511.000000   
mean        -4986.120328     -2994.202373      12.061091       0.999997   
std          3522.886321      1509.450419      11.944812       0.001803   
min        -24672.000000     -7197.000000       0.000000       0.000000   
25%         -7479.500000     -4299.000000       5.000000       1.000000   
50%         -4504.000000     -3254.000000       9.000000       1.000000   
75%         -2010.000000     -1720.000000      15.000000       1.000000   
max             0.000000         0.000000      91.000000       1.000000   

       FLAG_EMP_PHONE  FLAG_WORK_PHONE  FLAG_CONT_MOBILE     FLAG_PHONE  \
count   307511.000000    307511.000000     307511.000000  307511.000000   
mean         0.819889         0.199368          0.998133       0.281066   
std          0.384280         0.399526          0.043164       0.449521   
min          0.000000         0.000000          0.000000       0.000000   
25%          1.000000         0.000000          1.000000       0.000000   
50%          1.000000         0.000000          1.000000       0.000000   
75%          1.000000         0.000000          1.000000       1.000000   
max          1.000000         1.000000          1.000000       1.000000   

          FLAG_EMAIL  CNT_FAM_MEMBERS  REGION_RATING_CLIENT  \
count  307511.000000    307509.000000         307511.000000   
mean        0.056720         2.152665              2.052463   
std         0.231307         0.910682              0.509034   
min         0.000000         1.000000              1.000000   
25%         0.000000         2.000000              2.000000   
50%         0.000000         2.000000              2.000000   
75%         0.000000         3.000000              2.000000   
max         1.000000        20.000000              3.000000   

       REGION_RATING_CLIENT_W_CITY  HOUR_APPR_PROCESS_START  \
count                307511.000000            307511.000000   
mean                      2.031521                12.063419   
std                       0.502737                 3.265832   
min                       1.000000                 0.000000   
25%                       

In [7]:
app_test.describe()

SK_ID_CURR  CNT_CHILDREN  AMT_INCOME_TOTAL    AMT_CREDIT  \
count   48744.000000  48744.000000      4.874400e+04  4.874400e+04   
mean   277796.676350      0.397054      1.784318e+05  5.167404e+05   
std    103169.547296      0.709047      1.015226e+05  3.653970e+05   
min    100001.000000      0.000000      2.694150e+04  4.500000e+04   
25%    188557.750000      0.000000      1.125000e+05  2.606400e+05   
50%    277549.000000      0.000000      1.575000e+05  4.500000e+05   
75%    367555.500000      1.000000      2.250000e+05  6.750000e+05   
max    456250.000000     20.000000      4.410000e+06  2.245500e+06   

         AMT_ANNUITY  AMT_GOODS_PRICE  REGION_POPULATION_RELATIVE  \
count   48720.000000     4.874400e+04                48744.000000   
mean    29426.240209     4.626188e+05                    0.021226   
std     16016.368315     3.367102e+05                    0.014428   
min      2295.000000     4.500000e+04                    0.000253   
25%     17973.000000     2.250000e+05                    0.010006   
50%     26199.000000     3.960000e+05                    0.018850   
75%     37390.500000     6.300000e+05                    0.028663   
max    180576.000000     2.245500e+06                    0.072508   

         DAYS_BIRTH  DAYS_EMPLOYED  DAYS_REGISTRATION  DAYS_ID_PUBLISH  \
count  48744.000000   48744.000000       48744.000000     48744.000000   
mean  -16068.084605   67485.366322       -4967.652716     -3051.712949   
std     4325.900393  144348.507136        3552.612035      1569.276709   
min   -25195.000000  -17463.000000      -23722.000000     -6348.000000   
25%   -19637.000000   -2910.000000       -7459.250000     -4448.000000   
50%   -15785.000000   -1293.000000       -4490.000000     -3234.000000   
75%   -12496.000000    -296.000000       -1901.000000     -1706.000000   
max    -7338.000000  365243.000000           0.000000         0.000000   

        OWN_CAR_AGE    FLAG_MOBIL  FLAG_EMP_PHONE  FLAG_WORK_PHONE  \
count  16432.000000  48744.000000    48744.000000     48744.000000   
mean      11.786027      0.999979        0.809720         0.204702   
std       11.462889      0.004529        0.392526         0.403488   
min        0.000000      0.000000        0.000000         0.000000   
25%        4.000000      1.000000        1.000000         0.000000   
50%        9.000000      1.000000        1.000000         0.000000   
75%       15.000000      1.000000        1.000000         0.000000   
max       74.000000      1.000000        1.000000         1.000000   

       FLAG_CONT_MOBILE    FLAG_PHONE    FLAG_EMAIL  CNT_FAM_MEMBERS  \
count      48744.000000  48744.000000  48744.000000     48744.000000   
mean           0.998400      0.263130      0.162646         2.146767   
std            0.039971      0.440337      0.369046         0.890423   
min            0.000000      0.000000      0.000000         1.000000   
25%            1.000000      0.000000      0.000000         2.000000   
50%            1.000000      0.000000      0.000000         2.000000   
75%            1.000000      1.000000      0.000000         3.000000   
max            1.000000      1.000000      1.000000        21.000000   

       REGION_RATING_CLIENT  REGION_RATING_CLIENT_W_CITY  \
count          48744.000000                 48744.000000   
mean               2.038159                     2.012596   
std                0.522694                     0.515804   
min                1.000000                    -1.000000   
25%                2.000000                     2.000000   
50%                2.000000                     2.000000   
75%                2.000000                     2.000000   
max                3.000000                     3.000000   

       HOUR_APPR_PROCESS_START  REG_REGION_NOT_LIVE_REGION  \
count             48744.000000                48744.000000   
mean                 12.007365                    0.018833   
std                   3.278172                    0.135937   
min                  

In [8]:
app_train.isnull().sum()

SK_ID_CURR                           0
TARGET                               0
NAME_CONTRACT_TYPE                   0
CODE_GENDER                          0
FLAG_OWN_CAR                         0
FLAG_OWN_REALTY                      0
CNT_CHILDREN                         0
AMT_INCOME_TOTAL                     0
AMT_CREDIT                           0
AMT_ANNUITY                         12
AMT_GOODS_PRICE                    278
NAME_TYPE_SUITE                   1292
NAME_INCOME_TYPE                     0
NAME_EDUCATION_TYPE                  0
NAME_FAMILY_STATUS                   0
NAME_HOUSING_TYPE                    0
REGION_POPULATION_RELATIVE           0
DAYS_BIRTH                           0
DAYS_EMPLOYED                        0
DAYS_REGISTRATION                    0
DAYS_ID_PUBLISH                      0
OWN_CAR_AGE                     202929
FLAG_MOBIL                           0
FLAG_EMP_PHONE                       0
FLAG_WORK_PHONE                      0
FLAG_CONT_MOBILE         

In [9]:
app_train.shape

(307511, 122)

In [10]:
app_test.shape

(48744, 121)

In [11]:
#DAYS_BIRTHを正式な年齢に変換しただけ
app_train['DAYS_BIRTH'] = app_train['DAYS_BIRTH']*-1/365
app_test['DAYS_BIRTH'] = app_test['DAYS_BIRTH']*-1/365

In [12]:
app_train1 = app_train.loc[:, ['SK_ID_CURR', 'AMT_INCOME_TOTAL','DAYS_BIRTH', 'TARGET']]
app_test1 = app_test.loc[:, ['SK_ID_CURR', 'AMT_INCOME_TOTAL','DAYS_BIRTH']]

In [13]:
from sklearn.model_selection import train_test_split

#学習データと検証データに分ける
X_train, X_test, Y_train, Y_test = train_test_split(np.array(app_train1.iloc[:, [0, 1, 2]])
                                                         , np.array(app_train1.iloc[:, [3]]), random_state = 0)

print(X_train.shape)

(230633, 3)


In [14]:
Y_train = Y_train.reshape(-1)
Y_test = Y_test.reshape(-1)

In [15]:
# ランダムフォレストで学習
from sklearn import tree
clf = tree.DecisionTreeClassifier()
clf.fit(X_train, Y_train)
Y_pred= clf.predict_proba(X_test)[:, 1]

from sklearn.metrics import roc_auc_score
print('rocスコア:', roc_auc_score(Y_test, Y_pred))

rocスコア: 0.5037940144657429


In [16]:
Y_pred2 = clf.predict_proba(app_test1)[:, 1]

## 【問題3】テストデータに対する推定
テストデータ（application_test.csv）に対して推定を行い、Kaggleに提出を行ってください。


正しく提出が行えていれば、精度は低くても構いません。

In [206]:
#array型にしないとあとでデータフレームに出来ない
app_test2 = np.array(app_test1).astype(np.int)


In [18]:
#array型同士を、予測データとIDデータで繋げて、インデックスの位置を戻してから、それぞれの列に名前を付け直す
submission = pd.DataFrame(Y_pred2, app_test2[:, 0]).reset_index().rename(columns={0:'TARGET','index' :'SK_ID_CURR'})

In [19]:
#ここの左にあるインデックスを、下のindex=Falseで削除しにいっている
submission

SK_ID_CURR  TARGET
0          100001     0.0
1          100005     0.0
2          100013     0.0
3          100028     1.0
4          100038     0.0
5          100042     0.0
6          100057     0.0
7          100065     0.0
8          100066     1.0
9          100067     0.0
10         100074     0.0
11         100090     0.0
12         100091     0.0
13         100092     0.0
14         100106     0.0
15         100107     0.0
16         100109     0.0
17         100117     0.0
18         100128     0.0
19         100141     0.0
20         100150     0.0
21         100168     0.0
22         100169     0.0
23         100170     0.0
24         100171     0.0
25         100172     0.0
26         100184     0.0
27         100187     0.0
28         100212     0.0
29         100222     0.0
30         100223     0.0
31         100232     0.0
32         100241     0.0
33         100245     1.0
34         100253     0.0
35         100256     0.0
36         100271     0.0
37         100278     0.0
38         100280     0.0
39         100306     0.0
40         100311     0.0
41         100312     0.0
42         100330     0.0
43         100331     0.0
44         100352     0.0
45         100358     0.0
46         100367     0.0
47         100382     0.0
48         100384     0.0
49         100385     0.0
50         100386     1.0
51         100399     0.0
52         100404     0.0
53         100416     0.0
54         100422     0.0
55         100426     0.0
56         100438     0.0
57         100444     0.0
58         100445     0.0
59         100446     0.0
60         100447     0.0
61         100450     0.0
62         100466     0.0
63         100483     0.0
64         100484     1.0
65         100494     0.0
66         100510     0.0
67         100512     0.0
68         100517     0.0
69         100548     0.0
70         100551     0.0
71         100552     0.0
72         100553     0.0
73         100561     0.0
74         100568     0.0
75         100569     1.0
76         100591     0.0
77         100592     0.0
78         100602     0.0
79         100607     0.0
80         100613     0.0
81         100617     0.0
82         100618     1.0
83         100622     0.0
84         100625     0.0
85         100677     0.0
86         100699     0.0
87         100702     0.0
88         100711     0.0
89         100729     0.0
90         100740     0.0
91         100744     0.0
92         100745     0.0
93         100747     0.0
94         100751     0.0
95         100752     0.0
96         100753     0.0
97         100754     0.0
98         100760     0.0
99         100762     0.0
100        100763     0.0
101        100765     0.0
102        100770     0.0
103        100772     0.0
104        100777     0.0
105        100791     0.0
106        100792     0.0
107        100797     0.0
108        100823     0.0
109        100826     0.0
110        100830     0.0
111        100836     1.0
112        100872     0.0
113        100910     0.0
114        100913     0.0
115        100918     1.0
116        100931     0.0
117        100952     0.0
118        100953     0.0
119        100965     0.0
120        100970     0.0
121        100982     0.0
122        100983     0.0
123        100984     1.0
124        100987     0.0
125        100997     0.0
126        100998     0.0
127        101002     0.0
128        101005     0.0
129        101008     0.0
130        101020     0.0
131        101021     0.0
132        101024     0.0
133        101025     0.0
134        101026     0.0
135        101031     1.0
136        101041     0.0
137        101051     0.0
138        101055     0.0
139        101056     0.0
140        101057     0.0
141        101064     0.0
142        101079     0.0
143        101087     0.0
144        101090     0.0
145        101092     0.0
146        101097     0.0
147        101099     0.0
148        101107     0.0
149        101118     0.0
150        101125     0.0
151        101126     0.0
152        101128     0.0
153

In [20]:
submission.to_csv('homecreditdata.csv', index= False)

#### 特徴量エンジニアリング

ベースラインモデルを元に、入力する特徴量に様々な工夫を行い精度を向上させていきます。

## 【問題4】特徴量エンジニアリング
精度を上げるために以下のような観点で 特徴量エンジニアリング（Feature Engineering） を行ってください。


- どの特徴量を使うか
- どう前処理をするか

何をした時に検証データに対する評価指標がどのようになったかをまとめてください。最低5パターンの学習・検証を行ってください。


精度が高かったものに関してはテストデータに対しても推定を行い、Kaggleに提出を行ってください。



## ①rocスコア: 0.5101065828579237
#### 欠損値が入っている全行削除、相関係数のヒートマップで繋がりがりそうなものをピックアップ、決定木で学習

## 欠損値のデータを確認している

In [28]:
total = app_train.isnull().sum().sort_values(ascending=False)
total1 = app_test.isnull().sum().sort_values(ascending=False)
print(total)
print(total1)

COMMONAREA_MEDI                 214865
COMMONAREA_AVG                  214865
COMMONAREA_MODE                 214865
NONLIVINGAPARTMENTS_MODE        213514
NONLIVINGAPARTMENTS_MEDI        213514
NONLIVINGAPARTMENTS_AVG         213514
FONDKAPREMONT_MODE              210295
LIVINGAPARTMENTS_MEDI           210199
LIVINGAPARTMENTS_MODE           210199
LIVINGAPARTMENTS_AVG            210199
FLOORSMIN_MEDI                  208642
FLOORSMIN_MODE                  208642
FLOORSMIN_AVG                   208642
YEARS_BUILD_MEDI                204488
YEARS_BUILD_AVG                 204488
YEARS_BUILD_MODE                204488
OWN_CAR_AGE                     202929
LANDAREA_MODE                   182590
LANDAREA_AVG                    182590
LANDAREA_MEDI                   182590
BASEMENTAREA_MEDI               179943
BASEMENTAREA_AVG                179943
BASEMENTAREA_MODE               179943
EXT_SOURCE_1                    173378
NONLIVINGAREA_MEDI              169682
NONLIVINGAREA_AVG        

In [83]:
#とりあえず欠損値を含む特徴量を全削除
app_train2 = app_train.dropna(axis=0) 
app_test2 = app_test.dropna(axis=0)

In [70]:
# #saleprice correlation matrix
# k = 10 #number of variables for heatmap
# cols = app_train2.corr().nlargest(k, 'TARGET')['TARGET'].index
# cm = np.corrcoef(app_train2[cols].values.T)
# sns.set(font_scale=1.25)
# hm = sns.heatmap(cm, cbar=True, annot=True, square=True, fmt='.2f', annot_kws={'size': 10}, yticklabels=cols.values, xticklabels=cols.values)
# plt.show()

##### 欠損値削除→目的変数に対して相関係数が高いものの中で相関係数が高いもの同士などをピックアップして以下学習と推定を行う

In [31]:
app_train3 = app_train2.loc[:, ['SK_ID_CURR', 'DAYS_BIRTH','DAYS_EMPLOYED', 'REGION_RATING_CLIENT', 'OBS_60_CNT_SOCIAL_CIRCLE', 'TARGET']]

app_test3 = app_test2.loc[:, ['SK_ID_CURR', 'DAYS_BIRTH','DAYS_EMPLOYED', 'REGION_RATING_CLIENT', 'OBS_60_CNT_SOCIAL_CIRCLE']]


In [32]:
X_train2, X_test2, Y_train2, Y_test2 = train_test_split(np.array(app_train3.iloc[:, [0, 1, 2, 3, 4]])
                                                         , np.array(app_train3.iloc[:, [5]]), random_state = 0)

In [33]:
clf1 = tree.DecisionTreeClassifier()
clf1.fit(X_train2, Y_train2)
Y_pred3 = clf1.predict_proba(X_test2)[:, 1]

print('rocスコア:', roc_auc_score(Y_test2, Y_pred3))

rocスコア: 0.5101065828579237


#### 練習用に提出まで作ってみる

In [43]:
# Y_pred4 = clf1.predict_proba(app_test3)[:, 1]
# Y_pred4 = pd.Series(Y_pred4)
# app_test3 = app_test3.reset_index()
# submission1 = pd.concat([app_test3['SK_ID_CURR'], Y_pred4], axis =1)
# submission1.rename(columns={0:'TARGET'})

## ②rocスコア:0.5309039046220067
#### 欠損値全行削除データを利用、LightGBMで重要な特徴量を20抽出、決定木で学習

### LightGBMの作業

In [110]:
#行数表示が理想と違う動きなのでここで足掻いてみるも、変化なかった。一旦そのままにしておく
pd.set_option('display.max_columns',  100)
pd.set_option('display.max_rows',  100)
np.set_printoptions(threshold = 100)
np.set_printoptions( threshold = 100)
np.set_printoptions(threshold=np.inf)

In [100]:
#上記の欠損値削除のデータの中のオブジェクトタイプの列を抽出するためのコード
#lightgbmをやっていて、オブジェクトタイプを受け付けないとやっていて気がついた為
a = app_train2.dtypes[app_train2.dtypes !="object"].index

In [102]:
#無事ここで抽出完了
app_train2 = app_train2[a]

In [103]:
#インポートしてます。この前にアナコンダで要インストールでした
import lightgbm as lgb

In [146]:
# ここのサイトを参考に、lightgbmにチャレンジ
# https://mathmatical22.xyz/2020/04/12/%e3%80%90%e5%88%9d%e5%bf%83%e8%80%85%e5%90%91%e3%81%91%e3%80%91%e7%89%b9%e5%be%b4%e9%87%8f%e9%87%8d%e8%a6%81%e5%ba%a6%e3%81%ae%e7%ae%97%e5%87%ba-lightgbm-%e3%80%90python%e3%80%91%e3%80%90%e6%a9%9f/

In [104]:
# 特徴量重要度を棒グラフでプロットする関数 
def plot_feature_importance(df):
    n_features = len(df)                              # 特徴量数(説明変数の個数) 
    df_plot = df.sort_values('importance')            # df_importanceをプロット用に特徴量重要度を昇順ソート 
    f_importance_plot = df_plot['importance'].values  # 特徴量重要度の取得 
    plt.barh(range(n_features), f_importance_plot, align='center') 
    cols_plot = df_plot['feature'].values             # 特徴量の取得 
    plt.yticks(np.arange(n_features), cols_plot)      # x軸,y軸の値の設定
    plt.xlabel('Feature importance')                  # x軸のタイトル
    plt.ylabel('Feature')

In [105]:
# 説明変数,目的変数
X = app_train2.drop('TARGET', axis=1).values # 説明変数(CRIM以外の特徴量)
y = app_train2['TARGET'].values             # 目的変数(CRIM)

# トレーニングデータ,テストデータの分割
X_train, X_test, y_train, y_test = train_test_split(X, y,test_size=0.20, random_state=2)

In [147]:
lgb_train = lgb.Dataset(X_train, y_train)
lgb_eval = lgb.Dataset(X_test, y_test, reference=lgb_train) 

# LightGBM parameters
params = {
        'task': 'train',
        'boosting_type': 'gbdt',
        'objective': 'regression', # 目的 : 回帰  
        'metric': {'rmse'}, # 評価指標 : rsme(平均二乗誤差の平方根)
}

# モデルの学習
model = lgb.train(params,
                  train_set=lgb_train, # トレーニングデータの指定
                  valid_sets=lgb_eval, # 検証データの指定
                  )

[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.011842 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 10353
[LightGBM] [Info] Number of data points in the train set: 6881, number of used features: 94
[LightGBM] [Info] Start training from score 0.060747
[1]	valid_0's rmse: 0.241376
[2]	valid_0's rmse: 0.240839
[3]	valid_0's rmse: 0.240095
[4]	valid_0's rmse: 0.239861
[5]	valid_0's rmse: 0.239198
[6]	valid_0's rmse: 0.238983
[7]	valid_0's rmse: 0.238411
[8]	valid_0's rmse: 0.238169
[9]	valid_0's rmse: 0.238007
[10]	valid_0's rmse: 0.23786
[11]	valid_0's rmse: 0.237776
[12]	valid_0's rmse: 0.23741
[13]	valid_0's rmse: 0.237127
[14]	valid_0's rmse: 0.237257
[15]	valid_0's rmse: 0.237024
[16]	valid_0's rmse: 0.236686
[17]	valid_0's rmse: 0.236464
[18]	valid_0's rmse: 0.236283
[19]	valid_0's rmse: 0.236409
[20]	valid_0's rmse: 0.236503
[21]	valid_0's rmse: 0.236263
[22]	valid_0's rmse: 0.236282
[23]	v

In [111]:
# 特徴量重要度の算出 (データフレームで取得)
cols = list(app_train2.drop('TARGET',axis=1).columns)         # 特徴量名のリスト(目的変数CRIM以外)
f_importance = np.array(model.feature_importance()) # 特徴量重要度の算出
f_importance = f_importance / np.sum(f_importance)  # 正規化(必要ない場合はコメントアウト)
df_importance = pd.DataFrame({'feature':cols, 'importance':f_importance})
df_importance = df_importance.sort_values('importance', ascending=False) # 降順ソート
display(df_importance)

feature  importance
30       EXT_SOURCE_3    0.068333
28       EXT_SOURCE_1    0.064000
29       EXT_SOURCE_2    0.054667
9   DAYS_REGISTRATION    0.042000
0          SK_ID_CURR    0.039667
..                ...         ...
79    FLAG_DOCUMENT_2    0.000000
15   FLAG_CONT_MOBILE    0.000000
13     FLAG_EMP_PHONE    0.000000
12         FLAG_MOBIL    0.000000
87   FLAG_DOCUMENT_10    0.000000

[105 rows x 2 columns]

In [116]:
#このあたりから学習に向けての処理をスタート！上から20個までを抽出する
df_importance = df_importance[:20]

df_importance.feature.values

In [330]:
app_train4 = app_train2.loc[:, ['SK_ID_CURR', 'EXT_SOURCE_3', 'EXT_SOURCE_1', 'EXT_SOURCE_2',
       'DAYS_REGISTRATION', 'DAYS_EMPLOYED',
       'DAYS_ID_PUBLISH', 'DAYS_BIRTH', 'DAYS_LAST_PHONE_CHANGE',
       'AMT_ANNUITY', 'AMT_CREDIT', 'REGION_POPULATION_RELATIVE',
       'OWN_CAR_AGE', 'AMT_INCOME_TOTAL', 'COMMONAREA_MODE',
       'LANDAREA_AVG', 'TOTALAREA_MODE', 'LIVINGAREA_AVG',
       'COMMONAREA_AVG', 'AMT_REQ_CREDIT_BUREAU_YEAR','TARGET']]

# app_test4 = app_test2.loc[:, ['SK_ID_CURR', 'EXT_SOURCE_3', 'EXT_SOURCE_1', 'EXT_SOURCE_2',
#        'DAYS_REGISTRATION', 'DAYS_EMPLOYED',
#        'DAYS_ID_PUBLISH', 'DAYS_BIRTH', 'DAYS_LAST_PHONE_CHANGE',
#        'AMT_ANNUITY', 'AMT_CREDIT', 'REGION_POPULATION_RELATIVE',
#        'OWN_CAR_AGE', 'AMT_INCOME_TOTAL', 'COMMONAREA_MODE',
#        'LANDAREA_AVG', 'TOTALAREA_MODE', 'LIVINGAREA_AVG',
#        'COMMONAREA_AVG', 'AMT_REQ_CREDIT_BUREAU_YEAR']]

### 上記までで抽出作業完了！

In [331]:
X_train3, X_test3, Y_train3, Y_test3 = train_test_split(np.array(app_train4.iloc[:, :-1])
                                                         , np.array(app_train4.loc[:, 'TARGET']), random_state = 0)

In [332]:
clf2 = tree.DecisionTreeClassifier()
clf2.fit(X_train3, Y_train3)
Y_pred4 = clf2.predict_proba(X_test3)[:, 1]

print('rocスコア:', roc_auc_score(Y_test3, Y_pred4))

rocスコア: 0.5309039046220067


## ③rocスコア：0.518407747753903
#### ②で作った、抽出データに標準化処理して、ロジスティック回帰をしようとしたら、オブジェクトのタイプでエラーが出て、解消出来ず、一旦寝かす

#### スプリットした後に標準化しないとダメです。ラベルに標準化するのは直感的におかしいでしょう！そしたら出来ました。でもスコアは下がりました。ズーン。

In [333]:
X_train4, X_test4, Y_train4, Y_test4 = train_test_split(np.array(app_train4.iloc[:, :-1])
                                                         , np.array(app_train4.iloc[:, [-1]]), random_state = 0)

In [334]:
from sklearn.preprocessing import StandardScaler
sc = StandardScaler()


X_train4 = sc.fit_transform(X_train4)


#データフレーム化しておいた方がこの下がやりやすかったけど、そのうちいらないことに気がつきそう
#app_train4 = pd.DataFrame(app_train4)

In [336]:
from sklearn.linear_model import LogisticRegression # ロジスティック回帰
clf = LogisticRegression() #モデルの生成
clf.fit(X_train4, Y_train4)

Y_pred4 = clf.predict_proba(X_test4)[:, 1]

print('rocスコア:', roc_auc_score(Y_test4, Y_pred4))

rocスコア: 0.518407747753903


/Users/misakiryo/opt/anaconda3/lib/python3.8/site-packages/sklearn/utils/validation.py:72: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(**kwargs)


## ③rocスコア:0.5743039492128577
#### 元データに戻る、オブジェクトデータに良さそうな特徴量が多いのでそれも利用したくなる、初めてのOneHotEncoder、そこからLightGBMで20個抽出、元データには存在しない列を作ってるので、OHEのデータを使って20個抽出、ロジ回で学習に臨もNaNとか無限の値が多いと言われてしまう、謝りながらもNaNの列を削除し、12個(実質11個の列)になり再度学習

In [213]:
#勢いで欠損値を処理してしまったことにより、民衆からは圧政だと判断されてしまったようだ。
#不満が相次いだので、一旦元に戻し、元データから作業をし直す。ここから信頼をもう一度取り戻そう。
#なので、今回は全ての変数をしっかりと見極めていく為に、one_hot_encodingを取り入れる

from sklearn.preprocessing import OneHotEncoder
import pandas as pd
import numpy as np
from IPython.core.display import display

print("-----one hot表現する前------")
display(app_train)

app_train_hot  = pd.get_dummies(app_train)
#one_hot = pd.get_dummies(df['支払い種別'])
print("-----one hot表現後------")
display(one_hot)

-----one hot表現する前------


SK_ID_CURR  TARGET NAME_CONTRACT_TYPE CODE_GENDER FLAG_OWN_CAR  \
0           100002       1         Cash loans           M            N   
1           100003       0         Cash loans           F            N   
2           100004       0    Revolving loans           M            Y   
3           100006       0         Cash loans           F            N   
4           100007       0         Cash loans           M            N   
...            ...     ...                ...         ...          ...   
307506      456251       0         Cash loans           M            N   
307507      456252       0         Cash loans           F            N   
307508      456253       0         Cash loans           F            N   
307509      456254       1         Cash loans           F            N   
307510      456255       0         Cash loans           F            N   

       FLAG_OWN_REALTY  CNT_CHILDREN  AMT_INCOME_TOTAL  AMT_CREDIT  \
0                    Y             0          202500.0    406597.5   
1                    N             0          270000.0   1293502.5   
2                    Y             0           67500.0    135000.0   
3                    Y             0          135000.0    312682.5   
4                    Y             0          121500.0    513000.0   
...                ...           ...               ...         ...   
307506               N             0          157500.0    254700.0   
307507               Y             0           72000.0    269550.0   
307508               Y             0          153000.0    677664.0   
307509               Y             0          171000.0    370107.0   
307510               N             0          157500.0    675000.0   

        AMT_ANNUITY  AMT_GOODS_PRICE NAME_TYPE_SUITE      NAME_INCOME_TYPE  \
0           24700.5         351000.0   Unaccompanied               Working   
1           35698.5        1129500.0          Family         State servant   
2            6750.0         135000.0   Unaccompanied               Working   
3           29686.5         297000.0   Unaccompanied               Working   
4           21865.5         513000.0   Unaccompanied               Working   
...             ...              ...             ...                   ...   
307506      27558.0         225000.0   Unaccompanied               Working   
307507      12001.5         225000.0   Unaccompanied             Pensioner   
307508      29979.0         585000.0   Unaccompanied               Working   
307509      20205.0         319500.0   Unaccompanied  Commercial associate   
307510      49117.5         675000.0   Unaccompanied  Commercial associate   

                  NAME_EDUCATION_TYPE    NAME_FAMILY_STATUS  \
0       Secondary / secondary special  Single / not married   
1                    Higher education               Married   
2       Secondary / secondary special  Single / not married   
3       Secondary / secondary special        Civil marriage   
4       Secondary / secondary special  Single / not married   
...                               ...                   ...   
307506  Secondary / secondary special             Separated   
307507  Secondary / secondary special                 Widow   
307508               Higher education             Separated   
307509  Secondary / secondary special               Married   
307510               Higher education               Married   

        NAME_HOUSING_TYPE  REGION_POPULATION_RELATIVE  DAYS_BIRTH  \
0       House / apartment                    0.018801   25.920548   
1       House / apartment                    0.003541   45.931507   
2       House / apartment                    0.010032   52.180822   
3       House / apartment                    0.008019   52.068493   
4       House / apartment                    0.028663   54.608219   
...                   ...                         ...         ...   
307506       With parents                    0.032561   25.553425   
307507  House / apartment       

-----one hot表現後------


SK_ID_CURR  TARGET  CNT_CHILDREN  AMT_INCOME_TOTAL  AMT_CREDIT  \
0           100002       1             0          202500.0    406597.5   
1           100003       0             0          270000.0   1293502.5   
2           100004       0             0           67500.0    135000.0   
3           100006       0             0          135000.0    312682.5   
4           100007       0             0          121500.0    513000.0   
...            ...     ...           ...               ...         ...   
307506      456251       0             0          157500.0    254700.0   
307507      456252       0             0           72000.0    269550.0   
307508      456253       0             0          153000.0    677664.0   
307509      456254       1             0          171000.0    370107.0   
307510      456255       0             0          157500.0    675000.0   

        AMT_ANNUITY  AMT_GOODS_PRICE  REGION_POPULATION_RELATIVE  DAYS_BIRTH  \
0           24700.5         351000.0                    0.018801   25.920548   
1           35698.5        1129500.0                    0.003541   45.931507   
2            6750.0         135000.0                    0.010032   52.180822   
3           29686.5         297000.0                    0.008019   52.068493   
4           21865.5         513000.0                    0.028663   54.608219   
...             ...              ...                         ...         ...   
307506      27558.0         225000.0                    0.032561   25.553425   
307507      12001.5         225000.0                    0.025164   56.917808   
307508      29979.0         585000.0                    0.005002   41.002740   
307509      20205.0         319500.0                    0.005313   32.769863   
307510      49117.5         675000.0                    0.046220   46.180822   

        DAYS_EMPLOYED  DAYS_REGISTRATION  DAYS_ID_PUBLISH  OWN_CAR_AGE  \
0                -637            -3648.0            -2120          NaN   
1               -1188            -1186.0             -291          NaN   
2                -225            -4260.0            -2531         26.0   
3               -3039            -9833.0            -2437          NaN   
4               -3038            -4311.0            -3458          NaN   
...               ...                ...              ...          ...   
307506           -236            -8456.0            -1982          NaN   
307507         365243            -4388.0            -4090          NaN   
307508          -7921            -6737.0            -5150          NaN   
307509          -4786            -2562.0             -931          NaN   
307510          -1262            -5128.0             -410          NaN   

        FLAG_MOBIL  FLAG_EMP_PHONE  FLAG_WORK_PHONE  FLAG_CONT_MOBILE  \
0                1               1                0                 1   
1                1               1                0                 1   
2                1               1                1                 1   
3                1               1                0                 1   
4                1               1                0                 1   
...            ...             ...              ...               ...   
307506           1               1                0                 1   
307507           1               0                0                 1   
307508           1               1                0                 1   
307509           1               1                0                 1   
307510           1               1                1                 1   

        FLAG_PHONE  FLAG_EMAIL  CNT_FAM_MEMBERS  REGION_RATING_CLIENT  \
0                1           0              1.0                     2   
1                1           0              2.0                     1   
2                1           0              1.0                     2   
3                0           0              2.0                     2   
4                0         

In [214]:
X = app_train_hot.drop('TARGET', axis=1).values # 説明変数(CRIM以外の特徴量)
y = app_train_hot['TARGET'].values             # 目的変数(CRIM)

# トレーニングデータ,テストデータの分割
X_train, X_test, y_train, y_test = train_test_split(X, y,test_size=0.20, random_state=2)

In [215]:
lgb_train = lgb.Dataset(X_train, y_train)
lgb_eval = lgb.Dataset(X_test, y_test, reference=lgb_train) 

# LightGBM parameters
params = {
        'task': 'train',
        'boosting_type': 'gbdt',
        'objective': 'regression', # 目的 : 回帰  
        'metric': {'rmse'}, # 評価指標 : rsme(平均二乗誤差の平方根)
}

# モデルの学習
model = lgb.train(params,
                  train_set=lgb_train, # トレーニングデータの指定
                  valid_sets=lgb_eval, # 検証データの指定
                  )

[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.165198 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 11684
[LightGBM] [Info] Number of data points in the train set: 246008, number of used features: 235
[LightGBM] [Info] Start training from score 0.080778
[1]	valid_0's rmse: 0.270669
[2]	valid_0's rmse: 0.269487
[3]	valid_0's rmse: 0.268506
[4]	valid_0's rmse: 0.267704
[5]	valid_0's rmse: 0.267024
[6]	valid_0's rmse: 0.266443
[7]	valid_0's rmse: 0.265953
[8]	valid_0's rmse: 0.265533
[9]	valid_0's rmse: 0.265154
[10]	valid_0's rmse: 0.26484
[11]	valid_0's rmse: 0.264572
[12]	valid_0's rmse: 0.264321
[13]	valid_0's rmse: 0.264096
[14]	valid_0's rmse: 0.263892
[15]	valid_0's rmse: 0.263716
[16]	valid_0's rmse: 0.26359
[17]	valid_0's rmse: 0.263416
[18]	valid_0's rmse: 0.263276
[19]	valid_0's rmse: 0.263121
[20]	valid_0's rmse: 0.26298


In [216]:
# 特徴量重要度の算出 (データフレームで取得)
cols = list(app_train_hot.drop('TARGET',axis=1).columns)         # 特徴量名のリスト(目的変数CRIM以外)
f_importance = np.array(model.feature_importance()) # 特徴量重要度の算出
f_importance = f_importance / np.sum(f_importance)  # 正規化(必要ない場合はコメントアウト)
df_importance = pd.DataFrame({'feature':cols, 'importance':f_importance})
df_importance = df_importance.sort_values('importance', ascending=False) # 降順ソート
display(df_importance)

feature  importance
30                               EXT_SOURCE_3    0.098333
29                               EXT_SOURCE_2    0.096000
28                               EXT_SOURCE_1    0.087000
7                                  DAYS_BIRTH    0.054333
4                                 AMT_ANNUITY    0.045667
..                                        ...         ...
177                ORGANIZATION_TYPE_Cleaning    0.000000
106        NAME_CONTRACT_TYPE_Revolving loans    0.000000
174  ORGANIZATION_TYPE_Business Entity Type 1    0.000000
173                    ORGANIZATION_TYPE_Bank    0.000000
79                            FLAG_DOCUMENT_2    0.000000

[245 rows x 2 columns]

In [221]:
df_importance[:20].feature.values

array(['EXT_SOURCE_3', 'EXT_SOURCE_2', 'EXT_SOURCE_1', 'DAYS_BIRTH',
       'AMT_ANNUITY', 'AMT_CREDIT', 'DAYS_ID_PUBLISH', 'DAYS_EMPLOYED',
       'AMT_GOODS_PRICE', 'DAYS_LAST_PHONE_CHANGE', 'DAYS_REGISTRATION',
       'OWN_CAR_AGE', 'REGION_POPULATION_RELATIVE', 'SK_ID_CURR',
       'AMT_INCOME_TOTAL', 'HOUR_APPR_PROCESS_START', 'FLAG_DOCUMENT_3',
       'NAME_EDUCATION_TYPE_Higher education',
       'AMT_REQ_CREDIT_BUREAU_YEAR', 'AMT_REQ_CREDIT_BUREAU_QRT'],
      dtype=object)

In [223]:
b = 'EXT_SOURCE_3', 'EXT_SOURCE_2', 'EXT_SOURCE_1', 'DAYS_BIRTH','AMT_ANNUITY', 'AMT_CREDIT', 'DAYS_ID_PUBLISH', 'DAYS_EMPLOYED','AMT_GOODS_PRICE', 'DAYS_LAST_PHONE_CHANGE', 'DAYS_REGISTRATION','OWN_CAR_AGE', 'REGION_POPULATION_RELATIVE', 'AMT_INCOME_TOTAL', 'HOUR_APPR_PROCESS_START', 'FLAG_DOCUMENT_3','NAME_EDUCATION_TYPE_Higher education','AMT_REQ_CREDIT_BUREAU_YEAR', 'AMT_REQ_CREDIT_BUREAU_QRT'

In [240]:
app_train_hot1 = app_train_hot.loc[:, ['SK_ID_CURR', 'EXT_SOURCE_3', 'EXT_SOURCE_2', 'EXT_SOURCE_1', 'DAYS_BIRTH','AMT_ANNUITY', 'AMT_CREDIT', 'DAYS_ID_PUBLISH', 'DAYS_EMPLOYED','AMT_GOODS_PRICE', 'DAYS_LAST_PHONE_CHANGE', 'DAYS_REGISTRATION','OWN_CAR_AGE', 'REGION_POPULATION_RELATIVE', 'AMT_INCOME_TOTAL', 'HOUR_APPR_PROCESS_START', 'FLAG_DOCUMENT_3','NAME_EDUCATION_TYPE_Higher education','AMT_REQ_CREDIT_BUREAU_YEAR', 'AMT_REQ_CREDIT_BUREAU_QRT' ,'TARGET']]


In [235]:
#学習しようと思ったら　ValueError: Input contains NaN, infinity or a value too large for dtype('float64').が出るから以下の処理をしました
#https://qiita.com/twaka/items/eb3ff958f87ca1f4c971
app_train_hot1 = app_train_hot1.drop(app_train_hot1.columns[np.isnan(app_train_hot1).any()], axis=1)

In [236]:
X_train, X_test, Y_train, Y_test = train_test_split(np.array(app_train_hot1.iloc[:, :-1])
                                                         , np.array(app_train_hot1.loc[:, 'TARGET']), random_state = 0)

In [238]:
from sklearn.linear_model import LogisticRegression # ロジスティック回帰
clf3 = LogisticRegression() #モデルの生成
clf3.fit(X_train, Y_train)

Y_pred = clf3.predict_proba(X_test)[:, 1]

print('rocスコア:', roc_auc_score(Y_test, Y_pred))

rocスコア: 0.5743039492128577


## ④rocスコア:0.5905972673942013
#### ③の中でNaNへの対応が雑だと思う、逆に埋めるパターンで攻めてみる、平均値で試しに埋める、ついでにマイナスの値が気になるので処理する(rocが上がるのだけにする)、ロジ回で学習

In [244]:
print(app_train_hot1.isnull().sum())
print(app_train_hot1.shape)

SK_ID_CURR                                   0
EXT_SOURCE_3                             60965
EXT_SOURCE_2                               660
EXT_SOURCE_1                            173378
DAYS_BIRTH                                   0
AMT_ANNUITY                                 12
AMT_CREDIT                                   0
DAYS_ID_PUBLISH                              0
DAYS_EMPLOYED                                0
AMT_GOODS_PRICE                            278
DAYS_LAST_PHONE_CHANGE                       1
DAYS_REGISTRATION                            0
OWN_CAR_AGE                             202929
REGION_POPULATION_RELATIVE                   0
AMT_INCOME_TOTAL                             0
HOUR_APPR_PROCESS_START                      0
FLAG_DOCUMENT_3                              0
NAME_EDUCATION_TYPE_Higher education         0
AMT_REQ_CREDIT_BUREAU_YEAR               41519
AMT_REQ_CREDIT_BUREAU_QRT                41519
TARGET                                       0
dtype: int64


In [408]:
# 以下サイトに欠損値の簡易な対応がある。初めてなので平均値で埋めてみる。(説明変数のタイプを見極めて対応を変えたい。)
# https://rightcode.co.jp/blog/information-technology/missing-value-approach
app_hot_fillna = app_train_hot1.fillna(app_train_hot1.mean())

In [409]:
#app_hot_fillna['DAYS_ID_PUBLISH'] = app_hot_fillna['DAYS_ID_PUBLISH']*-1/365
app_hot_fillna['DAYS_EMPLOYED'] = app_hot_fillna['DAYS_EMPLOYED']*-1/365
app_hot_fillna['DAYS_LAST_PHONE_CHANGE'] = app_hot_fillna['DAYS_LAST_PHONE_CHANGE']*-1/365
#app_hot_fillna['DAYS_REGISTRATION'] = app_hot_fillna['DAYS_REGISTRATION']*-1/365

In [410]:
app_hot_fillna = round(app_hot_fillna, 4)

In [411]:
X_train, X_test, Y_train, Y_test = train_test_split(np.array(app_hot_fillna.iloc[:, :-1])
                                                         , np.array(app_hot_fillna.loc[:, 'TARGET']), random_state = 0)

In [412]:
from sklearn.linear_model import LogisticRegression # ロジスティック回帰
clf = LogisticRegression() #モデルの生成
clf.fit(X_train, Y_train)

Y_pred = clf.predict_proba(X_test)[:, 1]

print('rocスコア:', roc_auc_score(Y_test, Y_pred))

rocスコア: 0.5905972673942013


/Users/misakiryo/opt/anaconda3/lib/python3.8/site-packages/sklearn/linear_model/_logistic.py:762: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(


## ⑤rocスコア:0.5683507219487863
#### app_hot_fillnaに標準化してみると、下がる・・・

In [397]:
X_train, X_test, Y_train, Y_test = train_test_split(np.array(app_hot_fillna.iloc[:, :-1])
                                                         , np.array(app_hot_fillna.iloc[:, [-1]]), random_state = 0)

In [439]:
pd.DataFrame(X_test)

0       1       2       3        4        5          6       7   \
0      149741.0  0.1455  0.1827  0.4849  59.6548  20191.5   417024.0 -4653.0   
1      363290.0  0.6801  0.6691  0.6246  50.6822  31261.5   640080.0 -2028.0   
2      436006.0  0.1735  0.4543  0.5021  49.5452  45000.0   900000.0 -1616.0   
3      377703.0  0.4401  0.6881  0.5021  33.7507  33025.5  1125000.0 -4215.0   
4      188624.0  0.0817  0.4264  0.5021  27.8110  42840.0   835380.0 -2834.0   
...         ...     ...     ...     ...      ...      ...        ...     ...   
76873  446467.0  0.5109  0.4192  0.5021  27.2630  26640.0   545040.0  -872.0   
76874  173880.0  0.8214  0.7139  0.5346  34.4356  38362.5  1395000.0 -4506.0   
76875  343297.0  0.6430  0.6998  0.5021  56.6055  33642.0   481495.5 -2431.0   
76876  109230.0  0.4957  0.0445  0.5021  37.9726  24997.5   770913.0 -4718.0   
76877  292489.0  0.3556  0.4513  0.5765  30.6356  32242.5  1125000.0 -1194.0   

              8          9       10       11       12      13        14    15  \
0         5.8219   360000.0  5.5014  -4611.0  12.0611  0.0202  117000.0  13.0   
1         5.6301   450000.0  1.9945  -3052.0  12.0611  0.0462  450000.0  13.0   
2        11.3945   900000.0  3.4877  -8525.0   4.0000  0.0106  450000.0  14.0   
3         6.9370  1125000.0  2.6959 -12304.0   6.0000  0.0186  360000.0  15.0   
4         6.8932   675000.0 -0.0000  -2789.0   6.0000  0.0207  675000.0   7.0   
...          ...        ...     ...      ...      ...     ...       ...   ...   
76873     2.2685   450000.0  0.8630  -2495.0  12.0611  0.0188   99000.0   9.0   
76874    13.4630  1395000.0  1.4493  -6506.0  12.0611  0.0110  450000.0  11.0   
76875 -1000.6658   454500.0  0.9014  -4769.0  12.0611  0.0050  112500.0  11.0   
76876     2.2247   643500.0  0.1205  -4720.0  12.0611  0.0105  112500.0  10.0   
76877     0.7836  1125000.0  0.8575  -1179.0   0.0000  0.0152  157500.0  12.0   

        16   17   18      19  
0      1.0  0.0  3.0  0.0000  
1      1.0  1.0  1.0  0.0000  
2      0.0  1.0  0.0  2.0000  
3      1.0  0.0  1.0  0.0000  
4      0.0  0.0  2.0  0.0000  
...    ...  ...  ...     ...  
76873  1.0  0.0  1.9  0.2655  
76874  1.0  0.0  1.0  0.0000  
76875  1.0  0.0  0.0  0.0000  
76876  1.0  0.0  1.0  2.0000  
76877  1.0  1.0  1.0  0.0000  

[76878 rows x 20 columns]

In [379]:
from sklearn.preprocessing import StandardScaler
sc = StandardScaler()
X_train = sc.fit_transform(X_train)

In [380]:
from sklearn.linear_model import LogisticRegression # ロジスティック回帰
clf = LogisticRegression() #モデルの生成
clf.fit(X_train, Y_train)

Y_pred = clf.predict_proba(X_test)[:, 1]

print('rocスコア:', roc_auc_score(Y_test, Y_pred))

/Users/misakiryo/opt/anaconda3/lib/python3.8/site-packages/sklearn/utils/validation.py:72: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(**kwargs)


rocスコア: 0.5712201175824165


## 評価指標の動きに関して

- 欠損値があるデータを分析を仕切れずに削除するのは早計過ぎる。

- OneHotEncoding(OHE)を行うと上がる(オブジェクトタイプのデータに良いのが揃っているからか？)

- LightGBMを利用して重要項目を抽出すると上がる

- OHEして変数抽出後に標準化や正規化をしても大きく変化しづらい(既に変数の総数や値がまとまってきているからか)

- 少ない変数で学習、推定しても評価指標は上がらない

## 現状でのkaggle提出

In [406]:
app_test_hot  = pd.get_dummies(app_test)
#one_hot = pd.get_dummies(df['支払い種別'])
print("-----one hot表現後------")
display(app_test_hot)

-----one hot表現後------


SK_ID_CURR  CNT_CHILDREN  AMT_INCOME_TOTAL  AMT_CREDIT  AMT_ANNUITY  \
0          100001             0          135000.0    568800.0      20560.5   
1          100005             0           99000.0    222768.0      17370.0   
2          100013             0          202500.0    663264.0      69777.0   
3          100028             2          315000.0   1575000.0      49018.5   
4          100038             1          180000.0    625500.0      32067.0   
...           ...           ...               ...         ...          ...   
48739      456221             0          121500.0    412560.0      17473.5   
48740      456222             2          157500.0    622413.0      31909.5   
48741      456223             1          202500.0    315000.0      33205.5   
48742      456224             0          225000.0    450000.0      25128.0   
48743      456250             0          135000.0    312768.0      24709.5   

       AMT_GOODS_PRICE  REGION_POPULATION_RELATIVE  DAYS_BIRTH  DAYS_EMPLOYED  \
0             450000.0                    0.018850   52.715068          -2329   
1             180000.0                    0.035792   49.490411          -4469   
2             630000.0                    0.019101   54.898630          -4458   
3            1575000.0                    0.026392   38.290411          -1866   
4             625500.0                    0.010032   35.726027          -2191   
...                ...                         ...         ...            ...   
48739         270000.0                    0.002042   54.712329          -5169   
48740         495000.0                    0.035792   30.646575          -1149   
48741         315000.0                    0.026392   43.621918          -3037   
48742         450000.0                    0.018850   38.268493          -2731   
48743         270000.0                    0.006629   38.252055           -633   

       DAYS_REGISTRATION  DAYS_ID_PUBLISH  OWN_CAR_AGE  FLAG_MOBIL  \
0                -5170.0             -812          NaN           1   
1                -9118.0            -1623          NaN           1   
2                -2175.0            -3503          5.0           1   
3                -2000.0            -4208          NaN           1   
4                -4000.0            -4262         16.0           1   
...                  ...              ...          ...         ...   
48739            -9094.0            -3399          NaN           1   
48740            -3015.0            -3003          NaN           1   
48741            -2681.0            -1504          4.0           1   
48742            -1461.0            -1364          NaN           1   
48743            -1072.0            -4220         22.0           1   

       FLAG_EMP_PHONE  FLAG_WORK_PHONE  FLAG_CONT_MOBILE  FLAG_PHONE  \
0                   1                0                 1           0   
1                   1                0                 1           0   
2                   1                0                 1           0   
3                   1                0                 1           1   
4                   1                1                 1           0   
...               ...              ...               ...         ...   
48739               1                1                 1           1   
48740               1                0                 1           0   
48741               1                0                 1           1   
48742               1                1                 1           1   
48743               1                1                 1           0   

       FLAG_EMAIL  CNT_FAM_MEMBERS  REGION_RATING_CLIENT  \
0               1              2.0                     2   
1               0              2.0                     2   
2               0              2.0                     2   
3               0              4.0                     2   
4               0              3.0                     2   
...           ...              

In [407]:
app_test_hot1 = app_test_hot.loc[:, ['SK_ID_CURR', 'EXT_SOURCE_3', 'EXT_SOURCE_2', 'EXT_SOURCE_1', 'DAYS_BIRTH','AMT_ANNUITY', 'AMT_CREDIT', 'DAYS_ID_PUBLISH', 'DAYS_EMPLOYED','AMT_GOODS_PRICE', 'DAYS_LAST_PHONE_CHANGE', 'DAYS_REGISTRATION','OWN_CAR_AGE', 'REGION_POPULATION_RELATIVE', 'AMT_INCOME_TOTAL', 'HOUR_APPR_PROCESS_START', 'FLAG_DOCUMENT_3','NAME_EDUCATION_TYPE_Higher education','AMT_REQ_CREDIT_BUREAU_YEAR', 'AMT_REQ_CREDIT_BUREAU_QRT' ]]


In [416]:
app_test_hot1 = round(app_test_hot1, 4)


SK_ID_CURR  EXT_SOURCE_3  EXT_SOURCE_2  EXT_SOURCE_1  DAYS_BIRTH  \
0          100001        0.1595        0.7897        0.7526     52.7151   
1          100005        0.4330        0.2917        0.5650     49.4904   
2          100013        0.6110        0.6998           NaN     54.8986   
3          100028        0.6127        0.5097        0.5257     38.2904   
4          100038           NaN        0.4257        0.2021     35.7260   
...           ...           ...           ...           ...         ...   
48739      456221        0.6430        0.6486           NaN     54.7123   
48740      456222           NaN        0.6846           NaN     30.6466   
48741      456223        0.2837        0.6328        0.7335     43.6219   
48742      456224        0.5955        0.4457        0.3731     38.2685   
48743      456250        0.2721        0.4565           NaN     38.2521   

       AMT_ANNUITY  AMT_CREDIT  DAYS_ID_PUBLISH  DAYS_EMPLOYED  \
0          20560.5    568800.0             -812          -2329   
1          17370.0    222768.0            -1623          -4469   
2          69777.0    663264.0            -3503          -4458   
3          49018.5   1575000.0            -4208          -1866   
4          32067.0    625500.0            -4262          -2191   
...            ...         ...              ...            ...   
48739      17473.5    412560.0            -3399          -5169   
48740      31909.5    622413.0            -3003          -1149   
48741      33205.5    315000.0            -1504          -3037   
48742      25128.0    450000.0            -1364          -2731   
48743      24709.5    312768.0            -4220           -633   

       AMT_GOODS_PRICE  DAYS_LAST_PHONE_CHANGE  DAYS_REGISTRATION  \
0             450000.0                 -1740.0            -5170.0   
1             180000.0                     0.0            -9118.0   
2             630000.0                  -856.0            -2175.0   
3            1575000.0                 -1805.0            -2000.0   
4             625500.0                  -821.0            -4000.0   
...                ...                     ...                ...   
48739         270000.0                  -684.0            -9094.0   
48740         495000.0                     0.0            -3015.0   
48741         315000.0                  -838.0            -2681.0   
48742         450000.0                 -2308.0            -1461.0   
48743         270000.0                  -327.0            -1072.0   

       OWN_CAR_AGE  REGION_POPULATION_RELATIVE  AMT_INCOME_TOTAL  \
0              NaN                      0.0188          135000.0   
1              NaN                      0.0358           99000.0   
2              5.0                      0.0191          202500.0   
3              NaN                      0.0264          315000.0   
4             16.0                      0.0100          180000.0   
...            ...                         ...               ...   
48739          NaN                      0.0020          121500.0   
48740          NaN                      0.0358          157500.0   
48741          4.0                      0.0264          202500.0   
48742          NaN                      0.0188          225000.0   
48743         22.0                      0.0066          135000.0   

       HOUR_APPR_PROCESS_START  FLAG_DOCUMENT_3  \
0                           18                1   
1                            9                1   
2                           14                0   
3                           11                1   
4                            5                1   
...                        ...              ...   
48739                       16                0   
48740                       11                1   
48741                       12                1   
48742                       10                1   
48743                       14                1   

       NAME_EDUCATION_TYPE_Higher education  AMT_REQ_C

In [417]:
app_test_hot1 = app_test_hot1.fillna(app_test_hot1.mean())

In [421]:
Y_pred = clf.predict_proba(app_test_hot1)[:, 1]

pandas.core.frame.DataFrame

In [422]:
Y_pred = pd.Series(Y_pred)

In [428]:

#Y_pred4 = pd.Series(Y_pred4)
# app_test3 = app_test3.reset_index()
submission2 = pd.concat([app_test_hot1['SK_ID_CURR'], Y_pred], axis =1)
submission2.rename(columns={0:'TARGET'})


SK_ID_CURR    TARGET
0          100001  0.113823
1          100005  0.039948
2          100013  0.021560
3          100028  0.016645
4          100038  0.039027
...           ...       ...
48739      456221  0.009887
48740      456222  0.048505
48741      456223  0.027081
48742      456224  0.030005
48743      456250  0.055094

[48744 rows x 2 columns]

In [429]:
submission2.to_csv('homecreditdata1.csv', index= False)

## ⑥rocスコア:0.7539764568226368
#### 一からやり直してみる

In [453]:
from sklearn.metrics import accuracy_score # モデル評価用(正答率)
from sklearn.metrics import log_loss # モデル評価用(logloss)     
from sklearn.metrics import roc_auc_score # モデル評価用(auc)

In [442]:
#columnsのタイプをオブジェクトタイプとそれ以外で分けているコード
#後に欠損値の対応をする際に別れていると対応し易い
#tolistはリストに変換するという意味で、これでfor文が成り立っている

categorical_list = []
numerical_list = []
for i in application_train.columns.tolist():
    if application_train[i].dtype=='object':
        categorical_list.append(i)
    else:
        numerical_list.append(i)
print('Number of categorical features:', str(len(categorical_list)))
print('Number of numerical features:', str(len(numerical_list)))

Number of categorical features: 16
Number of numerical features: 106


In [443]:
categorical_list = []
numerical_list = []
for i in application_test.columns.tolist():
    if application_test[i].dtype=='object':
        categorical_list.append(i)
    else:
        numerical_list.append(i)
print('Number of categorical features:', str(len(categorical_list)))
print('Number of numerical features:', str(len(numerical_list)))

Number of categorical features: 16
Number of numerical features: 105


In [444]:
#欠損値を中央値で補完するのが=以降の式
from sklearn.impute import SimpleImputer
# from sklearn.preprocessing import Imputer
application_train[numerical_list] = SimpleImputer(strategy='median').fit_transform(application_train[numerical_list])

In [445]:
application_test[numerical_list] = SimpleImputer(strategy='median').fit_transform(application_test[numerical_list])

In [446]:
#gc.collectはメモリの解放？ってあるけど、重くならないようにしているものだと思う。数値の変化の問題ではない
#4行目はapplicationのオブジェクトデータをダミー変数に変換している
#drop_first=Trueは男性が1だったら女性は0という列を作らなくても男性が1の列にそれ以外を0という1列で済ますもの
#NaNの値はどうしてるんだろう・・・？

#del application_train; gc.collect()
application_train = pd.get_dummies(application_train, drop_first=True)
print(application_train.shape)

(307511, 230)


In [447]:
application_test = pd.get_dummies(application_test, drop_first=True)
print(application_test.shape)

(48744, 226)


In [448]:
import re
application_train = application_train.rename(columns = lambda x:re.sub('[^A-Za-z0-9_]+', '', x))

In [449]:
X = application_train.drop(['TARGET','CODE_GENDER_XNA', 'NAME_INCOME_TYPE_Maternityleave', 'NAME_FAMILY_STATUS_Unknown'], axis=1)
y = application_train.TARGET

In [450]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=.4)

In [451]:
import lightgbm as lgb

lgb_train = lgb.Dataset(X_train, y_train)
lgb_eval = lgb.Dataset(X_test, y_test, reference=lgb_train) 

i

# LightGBM parameters
params = {
        'task': 'train',
        'boosting_type': 'gbdt',
        'objective': 'regression', # 目的 : 回帰  
        'metric': {'rmse'}, # 評価指標 : rsme(平均二乗誤差の平方根)
}

# モデルの学習
model = lgb.train(params,
                  train_set=lgb_train, # トレーニングデータの指定
                  valid_sets=lgb_eval, # 検証データの指定
                  )

# テストデータの予測 (クラス1の予測確率(クラス1である確率)を返す)
y_pred_prob = model.predict(X_test)

[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.188679 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 11595
[LightGBM] [Info] Number of data points in the train set: 184506, number of used features: 218
[LightGBM] [Info] Start training from score 0.080805
[1]	valid_0's rmse: 0.270786
[2]	valid_0's rmse: 0.269573
[3]	valid_0's rmse: 0.268585
[4]	valid_0's rmse: 0.267743
[5]	valid_0's rmse: 0.267041
[6]	valid_0's rmse: 0.266466
[7]	valid_0's rmse: 0.265954
[8]	valid_0's rmse: 0.265497
[9]	valid_0's rmse: 0.265113
[10]	valid_0's rmse: 0.26477
[11]	valid_0's rmse: 0.264461
[12]	valid_0's rmse: 0.26418
[13]	valid_0's rmse: 0.263941
[14]	valid_0's rmse: 0.263726
[15]	valid_0's rmse: 0.263555
[16]	valid_0's rmse: 0.263367
[17]	valid_0's rmse: 0.26321
[18]	valid_0's rmse: 0.263056
[19]	valid_0's rmse: 0.262919
[20]	valid_0's rmse: 0.262816
[21]	valid_0's rmse: 0.262687
[22]	valid_0's rmse: 0.262593
[23]

In [455]:
# モデル評価
# # acc : 正答率
# acc = accuracy_score(y_test,y_pred)
# print('Acc :', acc)

# logloss 
logloss =  log_loss(y_test,y_pred_prob) # 引数 : log_loss(正解クラス,[クラス0の予測確率,クラス1の予測確率])
print('logloss :', logloss)

# AUC 
auc = roc_auc_score(y_test,y_pred_prob) # 引数 : roc_auc_score(正解クラス, クラス1の予測確率)
print('AUC :', auc) 

logloss : 0.25013110068179994
AUC : 0.7539764568226368


In [456]:
Y_pred = model.predict(application_test)

In [457]:
Y_pred = pd.DataFrame(Y_pred)

In [458]:
application_test['SK_ID_CURR'] = (application_test['SK_ID_CURR']).astype(int)

In [459]:
submission2 = pd.concat([application_test['SK_ID_CURR'], Y_pred.abs()], axis =1)

In [460]:
submission2.rename(columns={0:'TARGET'})

SK_ID_CURR    TARGET
0          100001  0.084906
1          100005  0.134604
2          100013  0.012343
3          100028  0.031443
4          100038  0.119319
...           ...       ...
48739      456221  0.030197
48740      456222  0.062207
48741      456223  0.055980
48742      456224  0.061220
48743      456250  0.187570

[48744 rows x 2 columns]

In [ ]:
submission2.to_csv('homecreditdata3.csv', index= False)